In [4]:
import numpy as np
import pandas as pd
import plotly.express as px
from tqdm import tqdm

In [5]:
# Load data
ancestry = pd.read_csv('preprocessed_data/ancestry.csv')
ancestry = ancestry.dropna()

In [6]:
# Load dummy data
dummy_data = [
    ['Ancient1', 'Modern1', -4.0, 40.0, 24.0, 55.0],
    ['Ancient2', 'Modern2', 6.0, 52.5, 25, 42.5]
]
columns = ['ancient', 'modern', 'ancient_lon', 'ancient_lat', 'modern_lon', 'modern_lat']
ancestry = pd.DataFrame(dummy_data, columns=columns)

In [7]:
# Function to add points to a map
def add_points_to_map(df, lat_col, lon_col, text_col, color='red', fig_existing=None):
    fig = px.scatter_geo(
        df,
        lat=lat_col,
        lon=lon_col,
        text=text_col,
        color_discrete_sequence=[color],
        size_max=15,
        projection='natural earth',
        hover_name=text_col
    )

    fig.update_traces(text=None)
    fig.update_geos(showland=True, landcolor='rgb(243, 243, 243)')

    fig.update_layout(
        geo=dict(
            scope='world',
            showland=True,
        )
    )

    if fig_existing:
        fig = fig_existing.add_trace(fig.data[0])

    return fig

In [8]:
def add_path_to_map(path, existing_fig, color='rgba(0, 255, 0, 0.5)'):
    df = pd.DataFrame()
    df['lat'] = path[:,0]
    df['lon'] = path[:,1]
    lines = px.line_geo(df, lat='lat', lon='lon').data[0]
    lines.update(line_color=color)
    existing_fig.add_trace(lines)
    existing_fig.add_trace(existing_fig.data[0])
    return existing_fig

In [9]:
# Brownian bridge function
def brownian_bridge(start, end, num_points=10, smoothness=0.2):
    # Generate random numbers following a normal distribution
    random_numbers = np.random.normal(0, 1, size=(num_points, 2))

    # Interpolate intermediate points
    points = [start]
    for i in range(num_points):
        weight = (i + 1) / (num_points + 1)
        scaling_factor = np.sqrt((1.0 - smoothness) * (1 - weight))
        intermediate_point = start + weight * (end - start) + scaling_factor * random_numbers[i]
        points.append(intermediate_point)

    # Include the end point
    points.append(end)

    return np.array(points)

In [10]:
# Plot map of sample brownian bridges for simulated points

# Add points to map
fig = add_points_to_map(ancestry, ancestry['ancient_lat'], ancestry['ancient_lon'], ancestry['ancient'], color='blue')
fig = add_points_to_map(ancestry, ancestry['modern_lat'], ancestry['modern_lon'], ancestry['modern'], color='orange', fig_existing=fig)

# Set figure size
fig.update_layout(
    width=1200,  # Specify the width in pixels
    height=700  # Specify the height in pixels
)

# Set initial zoom of the map
fig.update_geos(
    center=dict(lon=ancestry['ancient_lon'].mean(), lat=ancestry['ancient_lat'].mean()),
    projection_scale=4
)

# Add brownian bridge
for i in range(len(ancestry)):
    path = brownian_bridge(start=np.array([ancestry.iloc[i]['ancient_lat'], ancestry.iloc[i]['ancient_lon']]),
                    end=np.array([ancestry.iloc[i]['modern_lat'], ancestry.iloc[i]['modern_lon']]), 
                    num_points=100,
                    smoothness=0)
    add_path_to_map(path, fig)

fig.show()

In [83]:
# Plot map of sample brownian bridges for simulated points

# Add points to map
fig = add_points_to_map(ancestry, ancestry['ancient_lat'], ancestry['ancient_lon'], ancestry['ancient'], color='blue')
fig = add_points_to_map(ancestry, ancestry['modern_lat'], ancestry['modern_lon'], ancestry['modern'], color='orange', fig_existing=fig)

# Set figure size
fig.update_layout(
    width=1200,  # Specify the width in pixels
    height=700  # Specify the height in pixels
)

# Set initial zoom of the map
fig.update_geos(
    center=dict(lon=ancestry['ancient_lon'].mean(), lat=ancestry['ancient_lat'].mean()),
    projection_scale=4
)

# Add brownian bridge
n_bridges_per_pair = 100
for i in range(len(ancestry)):
    paths = [brownian_bridge(start=np.array([ancestry.iloc[i]['ancient_lat'], ancestry.iloc[i]['ancient_lon']]),
                    end=np.array([ancestry.iloc[i]['modern_lat'], ancestry.iloc[i]['modern_lon']]), 
                    num_points=100,
                    smoothness=0) for _ in range(n_bridges_per_pair)]
    for path in tqdm(paths):
        add_path_to_map(path, fig)

fig.show()

100%|██████████| 100/100 [00:02<00:00, 49.92it/s]


In [47]:
df = pd.DataFrame()
df['lat'] = np.array([path[:,0] for path in paths]).flatten()
df['lon'] = np.array([path[:,1] for path in paths]).flatten()

In [ ]:
# Not sure how to compute the PDF (should I have a probability for each point in the brownian bridge using a kernel density estimation (KDE) or some similar method?)
# And then to compute the probability of a brownian bridge I just integrate over the time domain?
